In [1]:
import os
import numpy as np
import pandas as pd
import alpaca_trade_api as tradeapi
from MCForecastTools import MCSimulation
from pathlib import Path
from dotenv import load_dotenv
import yfinance as yf
import panel as pn
from panel.interact import interact
import plotly.express as px
pn.extension('plotly')
import hvplot.pandas
import seaborn as sns

load_dotenv()
%matplotlib inline


Bad key "text.kerning_factor" on line 4 in
C:\Users\P\anaconda3\envs\pyvizenv\lib\site-packages\matplotlib\mpl-data\stylelib\_classic_test_patch.mplstyle.
You probably need to get an updated matplotlibrc file from
http://github.com/matplotlib/matplotlib/blob/master/matplotlibrc.template
or from the matplotlib source distribution


In [2]:
tickers = [
          "^GSPC",
          "GC=F",
          "CL=F",
          "SI=F",
          "DX-Y.NYB"
          ]

df_data = yf.download(tickers,
start="2000-09-01",
#end="2021-01-29",
progress=False,
interval = "1d",
index_col = "Date",
infer_datetime_format= True,
parse_dates = True,                    
groupby = "column"
                )

In [3]:
df_data.drop(columns=['Open', 'High', 'Low', 'Volume', 'Adj Close'], inplace=True)

In [4]:
df_data.rename(columns=
          {"CL=F":"crudeoil",
           "DX-Y.NYB":"usd",
           "GC=F":"gold",
           "SI=F":"silver",
           "^GSPC":"sp500",
           "Close":"close",
           "High":"high",
           "Low":"low",
           "Open":"open",
           "Volume":"volume"
            },inplace=True)

In [5]:
df_data.columns = df_data.columns.droplevel(level=0)
df_data.dropna(inplace=True)

In [6]:
df_data_return = df_data.pct_change()
df_data_return["portfolio_even_dist"] = (df_data_return["crudeoil"]*1)+(df_data_return["usd"]*1)+(df_data_return["gold"]*1)+(df_data_return["silver"]*1)
df_data_return["portfolio_2"] = (df_data_return["crudeoil"]*1)+(df_data_return["usd"]*0)+(df_data_return["gold"]*0)+(df_data_return["silver"]*1)

In [7]:
df_data_corr = df_data_return.corr()


In [8]:
df_data_rolling_corr = df_data_return.rolling(window=30).corr().dropna()
df_data_rolling_corr.reset_index(inplace=True)
df_data_rolling_corr.set_index("Date",inplace=True)

In [9]:
crudeoil_rolling_corr = pd.DataFrame(df_data_rolling_corr[df_data_rolling_corr['level_1'] == 'crudeoil'].sp500)
usd_rolling_corr = pd.DataFrame(df_data_rolling_corr[df_data_rolling_corr['level_1'] == 'usd'].sp500)
gold_rolling_corr = pd.DataFrame(df_data_rolling_corr[df_data_rolling_corr['level_1'] == 'gold'].sp500)
silver_rolling_corr = pd.DataFrame(df_data_rolling_corr[df_data_rolling_corr['level_1'] == 'silver'].sp500)
portfolio_even_dist_rolling_corr = pd.DataFrame(df_data_rolling_corr[df_data_rolling_corr['level_1'] == 'portfolio_even_dist'].sp500)
portfolio_2_rolling_corr = pd.DataFrame(df_data_rolling_corr[df_data_rolling_corr['level_1'] == 'portfolio_2'].sp500)
df_rolling_corr = pd.concat([crudeoil_rolling_corr,usd_rolling_corr,gold_rolling_corr,silver_rolling_corr,portfolio_even_dist_rolling_corr,portfolio_2_rolling_corr],join="inner",axis="columns")
df_rolling_corr.columns=["crudeoil","usd","gold","silver","portfolio_even_dist","portfolio_2"]

In [10]:
cumulative_return = ((1+df_data_return).cumprod() -1)

In [11]:
df_data_rolling_cov = df_data_return["portfolio_2"].rolling(window=30).cov(df_data_return["sp500"])
df_data_rolling_var = df_data_return["sp500"].rolling(window=30).var()
df_data_rolling_beta = df_data_rolling_cov / df_data_rolling_var

In [12]:
def data_correlation():
    data_corr = df_data_corr.hvplot.heatmap(title = "Commodities and Indices Correlation")    
    return data_corr

list_of_portfolio = ["gold","usd","silver","crudeoil","portfolio_even_dist","portfolio_2"]
def portfolio_cumulative_return(portfolio):
    port_cumulative_return = cumulative_return[["sp500",portfolio]].hvplot.line(title = f"{portfolio} Return and S&P500",
                                                                           xlabel="Date", ylabel="Monthly Close Price")
    return port_cumulative_return
def portfolio_correlation(portfolio):
    portfolio_corr = df_data_rolling_corr[df_data_rolling_corr['level_1'] == portfolio].sp500
    return portfolio_corr.hvplot.line(title = f"{portfolio} & S&P500 30 Days Rolling Correlation", xlabel="Date", ylabel="Correlation")

def portfolio_beta(portfolio):
    port_beta = (df_data_return[portfolio].rolling(window=30).cov(df_data_return["sp500"])) / df_data_rolling_var
    return port_beta.hvplot.line (title = f"{portfolio} & S&P500 30 Days Rolling Beta", xlabel="Date", ylabel="Beta")

In [13]:
portfolio_summary = pn.Column("#S&P 500 and Portfolios Summary", cumulative_return.hvplot(), data_correlation())
portfolio_analysis = pn.Column("#Portfolio Analysis", 
                               interact(portfolio_cumulative_return, portfolio=list_of_portfolio), 
                               interact(portfolio_correlation,portfolio=list_of_portfolio),
                               interact(portfolio_beta,portfolio=list_of_portfolio))
panel1=pn.Tabs(("Commodities Summary",portfolio_summary), ("Commodities Analysis",portfolio_analysis))


In [14]:
df_data_corr

crudeoil       usd      gold    silver     sp500  \
crudeoil             1.000000 -0.090327  0.092035  0.115412  0.139542   
usd                 -0.090327  1.000000 -0.405588 -0.373051 -0.079388   
gold                 0.092035 -0.405588  1.000000  0.782418 -0.019866   
silver               0.115412 -0.373051  0.782418  1.000000  0.099868   
sp500                0.139542 -0.079388 -0.019866  0.099868  1.000000   
portfolio_even_dist  0.897411 -0.188299  0.472447  0.525227  0.140691   
portfolio_2          0.942447 -0.207190  0.346528  0.440890  0.159705   

                     portfolio_even_dist  portfolio_2  
crudeoil                        0.897411     0.942447  
usd                            -0.188299    -0.207190  
gold                            0.472447     0.346528  
silver                          0.525227     0.440890  
sp500                           0.140691     0.159705  
portfolio_even_dist             1.000000     0.987693  
portfolio_2                     0.987693     1.000000

In [15]:
panel1.servable()

Tabs
    [0] Column
        [0] Markdown(str)
        [1] HoloViews(NdOverlay)
        [2] HoloViews(HeatMap)
    [1] Column
        [0] Markdown(str)
        [1] Column
            [0] Column
                [0] Select(name='portfolio', options=['gold', 'usd', ...], value='gold')
            [1] Row
                [0] HoloViews(NdOverlay, name='interactive01751')
        [2] Column
            [0] Column
                [0] Select(name='portfolio', options=['gold', 'usd', ...], value='gold')
            [1] Row
                [0] HoloViews(Curve, name='interactive01858')
        [3] Column
            [0] Column
                [0] Select(name='portfolio', options=['gold', 'usd', ...], value='gold')
            [1] Row
                [0] HoloViews(Curve, name='interactive01942')

In [16]:
cumulative_return[["sp500","portfolio_2"]].hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)